# Load Gensim Library

In [0]:
import gensim

In [0]:
import pandas as pd
import re, string
import gensim
import logging

In [0]:
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

# Load Text Data

In [0]:
# your_local_path="C:/Users/tejks/Desktop/ML/practice/"

In [0]:
#df = pd.read_csv(your_local_path+'unlabeledTrainData.tsv', header=0, delimiter="\t", quoting=3)

In [0]:
df = pd.read_csv('https://raw.githubusercontent.com/MatthieuBizien/Bag-popcorn/master/labeledTrainData.tsv',header=0, delimiter="\t", quoting=3)

In [7]:
df.shape

(25000, 3)

In [8]:
df.head()

id  sentiment                                             review
0  "5814_8"          1  "With all this stuff going down at the moment ...
1  "2381_9"          1  "\"The Classic War of the Worlds\" by Timothy ...
2  "7759_3"          0  "The film starts with a manager (Nicholas Bell...
3  "3630_4"          0  "It must be assumed that those who praised thi...
4  "9495_8"          1  "Superbly trashy and wondrously unpretentious ...

# Function to Clean up data

In [0]:
def clean_str(string):
  """
  String cleaning before vectorization
  """
  try:    
    string = re.sub(r'^https?:\/\/<>.*[\r\n]*', '', string, flags=re.MULTILINE)
    string = re.sub(r"[^A-Za-z]", " ", string)         
    words = string.strip().lower().split()    
    words = [w for w in words if len(w)>=1]
    return " ".join(words)	
  except:
    return ""

Clean the Data using routine above

In [0]:
df['clean_review'] = df['review'].apply(clean_str)

In [11]:
df.head()

id  ...                                       clean_review
0  "5814_8"  ...  with all this stuff going down at the moment w...
1  "2381_9"  ...  the classic war of the worlds by timothy hines...
2  "7759_3"  ...  the film starts with a manager nicholas bell g...
3  "3630_4"  ...  it must be assumed that those who praised this...
4  "9495_8"  ...  superbly trashy and wondrously unpretentious s...

[5 rows x 4 columns]

# Convert Each Review to a Word List before feeding to Word2Vec

In [0]:
documents = []

In [0]:
for doc in df['clean_review']:
    documents.append(doc.split(' '))

In [15]:
documents

[['with',
  'all',
  'this',
  'stuff',
  'going',
  'down',
  'at',
  'the',
  'moment',
  'with',
  'mj',
  'i',
  've',
  'started',
  'listening',
  'to',
  'his',
  'music',
  'watching',
  'the',
  'odd',
  'documentary',
  'here',
  'and',
  'there',
  'watched',
  'the',
  'wiz',
  'and',
  'watched',
  'moonwalker',
  'again',
  'maybe',
  'i',
  'just',
  'want',
  'to',
  'get',
  'a',
  'certain',
  'insight',
  'into',
  'this',
  'guy',
  'who',
  'i',
  'thought',
  'was',
  'really',
  'cool',
  'in',
  'the',
  'eighties',
  'just',
  'to',
  'maybe',
  'make',
  'up',
  'my',
  'mind',
  'whether',
  'he',
  'is',
  'guilty',
  'or',
  'innocent',
  'moonwalker',
  'is',
  'part',
  'biography',
  'part',
  'feature',
  'film',
  'which',
  'i',
  'remember',
  'going',
  'to',
  'see',
  'at',
  'the',
  'cinema',
  'when',
  'it',
  'was',
  'originally',
  'released',
  'some',
  'of',
  'it',
  'has',
  'subtle',
  'messages',
  'about',
  'mj',
  's',
  'feeling'

# Build the Model

In [16]:
#Build the model
model = gensim.models.Word2Vec(documents, #Word list
                               min_count=10, #Ignore all words with total frequency lower than this                           
                               workers=4, #Number of CPUs
                               size=50,  #Embedding size
                               window=5, #Maximum Distance between current and predicted word
                               iter=10   #Number of iterations over the text corpus
                              )  

2019-10-22 05:37:28,125 : WARNING : consider setting layer size to a multiple of 4 for greater performance
2019-10-22 05:37:28,128 : INFO : collecting all words and their counts
2019-10-22 05:37:28,129 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2019-10-22 05:37:28,593 : INFO : PROGRESS: at sentence #10000, processed 2427015 words, keeping 51094 word types
2019-10-22 05:37:29,079 : INFO : PROGRESS: at sentence #20000, processed 4829879 words, keeping 67006 word types
2019-10-22 05:37:29,311 : INFO : collected 73272 word types from a corpus of 6023662 raw words and 25000 sentences
2019-10-22 05:37:29,312 : INFO : Loading a fresh vocabulary
2019-10-22 05:37:29,409 : INFO : effective_min_count=10 retains 19874 unique words (27% of original 73272, drops 53398)
2019-10-22 05:37:29,410 : INFO : effective_min_count=10 leaves 5890724 word corpus (97% of original 6023662, drops 132938)
2019-10-22 05:37:29,474 : INFO : deleting the raw counts dictionary of 73272 it

# Exploring the model

How many words in the model and how many features

In [17]:
model.wv.syn0.shape

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `syn0` (Attribute will be removed in 4.0.0, use self.wv.vectors instead).
  """Entry point for launching an IPython kernel.


(19874, 50)

In [18]:
model.wv.vocab

{'with': <gensim.models.keyedvectors.Vocab at 0x7fe801bb87f0>,
 'all': <gensim.models.keyedvectors.Vocab at 0x7fe801efbac8>,
 'this': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217a20>,
 'stuff': <gensim.models.keyedvectors.Vocab at 0x7fe7ee2179b0>,
 'going': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217b70>,
 'down': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217978>,
 'at': <gensim.models.keyedvectors.Vocab at 0x7fe7ee2179e8>,
 'the': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217b00>,
 'moment': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217a58>,
 'mj': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217b38>,
 'i': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217ac8>,
 've': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217438>,
 'started': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217ba8>,
 'listening': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217be0>,
 'to': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217c18>,
 'his': <gensim.models.keyedvectors.Vocab at 0x7fe7ee217

Get an embedding for a word

In [19]:
model.wv['flower']

array([-2.28965402e-01, -2.24093899e-01,  1.28377032e+00, -5.70021451e-01,
        2.20062081e-02,  1.00662149e-01, -3.54240298e-01, -1.48919433e-01,
       -8.16836208e-02,  2.14797676e-01,  4.74928468e-01, -9.13029164e-02,
       -1.61665305e-01,  1.82789817e-01, -2.89094031e-01, -4.56252128e-01,
        2.02236027e-01,  1.78795725e-01,  2.41188049e-01,  2.84723282e-01,
        3.54540467e-01,  3.14390957e-01, -1.06692719e+00,  4.13977265e-01,
        1.08187944e-01, -1.00602776e-01,  7.01735467e-02,  1.26550004e-01,
        2.72914860e-02,  4.85369742e-01, -2.21314892e-01, -2.57857800e-01,
        1.05420826e-03,  4.18139994e-02, -6.88543618e-01,  9.80097890e-01,
       -8.39411393e-02, -8.91750455e-02, -1.47814465e+00,  1.56790748e-01,
        1.57108113e-01, -1.63973629e-01,  9.46514606e-01, -1.37416080e-01,
       -2.48181477e-01,  5.03169835e-01,  3.01531702e-01, -2.49607027e-01,
        2.24394575e-01, -1.33121192e-01], dtype=float32)

Saving the model

In [20]:
model.save('word2vec-movie-50')

2019-10-22 05:39:15,349 : INFO : saving Word2Vec object under word2vec-movie-50, separately None
2019-10-22 05:39:15,351 : INFO : not storing attribute vectors_norm
2019-10-22 05:39:15,353 : INFO : not storing attribute cum_table
/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:398: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL
2019-10-22 05:39:15,516 : INFO : saved word2vec-movie-50


Finding Words which have similar meaning

In [21]:
model.wv.most_similar('awful')

2019-10-22 05:39:25,227 : INFO : precomputing L2-norms of word weight vectors
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


[('horrible', 0.9228600263595581),
 ('terrible', 0.8978748917579651),
 ('atrocious', 0.8092063665390015),
 ('dreadful', 0.8062059283256531),
 ('bad', 0.7958945035934448),
 ('abysmal', 0.7952473163604736),
 ('horrendous', 0.7861732244491577),
 ('ridiculous', 0.7857023477554321),
 ('appalling', 0.7556474804878235),
 ('stupid', 0.7542984485626221)]

Find the Word which is not like others

In [23]:
model.doesnt_match("man woman child kitchen".split())

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `doesnt_match` (Method will be removed in 4.0.0, use self.wv.doesnt_match() instead).
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.6/dist-packages/gensim/models/keyedvectors.py:895: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  vectors = vstack(self.word_vec(word, use_norm=True) for word in used_words).astype(REAL)
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


'kitchen'

1. Equation king + man = queen + ?
2. In this case there may not be enough data for this equation

In [24]:
model.most_similar(positive=['king','man'], negative=['queen'])

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.
/usr/local/lib/python3.6/dist-packages/gensim/matutils.py:737: FutureWarning: Conversion of the second argument of issubdtype from `int` to `np.signedinteger` is deprecated. In future, it will be treated as `np.int64 == np.dtype(int).type`.
  if np.issubdtype(vec.dtype, np.int):


[('director', 0.5086256861686707),
 ('writer', 0.5065587162971497),
 ('boll', 0.4683820307254791),
 ('himself', 0.46780186891555786),
 ('guy', 0.45386019349098206),
 ('filmmaker', 0.45105960965156555),
 ('screenwriter', 0.45026710629463196),
 ('killer', 0.4370979070663452),
 ('author', 0.4348078966140747),
 ('whale', 0.4298858642578125)]

Loading a model from Memory

In [25]:
model = gensim.models.Word2Vec.load('word2vec-movie-50')

2019-10-22 05:45:51,892 : INFO : loading Word2Vec object from word2vec-movie-50
/usr/local/lib/python3.6/dist-packages/smart_open/smart_open_lib.py:398: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL
2019-10-22 05:45:52,197 : INFO : loading wv recursively from word2vec-movie-50.wv.* with mmap=None
2019-10-22 05:45:52,198 : INFO : setting ignored attribute vectors_norm to None
2019-10-22 05:45:52,199 : INFO : loading vocabulary recursively from word2vec-movie-50.vocabulary.* with mmap=None
2019-10-22 05:45:52,199 : INFO : loading trainables recursively from word2vec-movie-50.trainables.* with mmap=None
2019-10-22 05:45:52,200 : INFO : setting ignored attribute cum_table to None
2019-10-22 05:45:52,201 : INFO : loaded word2vec-movie-50
